In [1]:
import pandas as pd

In [14]:
df = pd.read_csv("data.csv")
df['Timestamp'] = pd.to_datetime(df['Timestamp'], unit='s', utc=True)
df.tail()

Timestamp     Open     High      Low    Close  \
7317754 2025-11-30 23:55:00+00:00  90405.0  90452.0  90403.0  90452.0   
7317755 2025-11-30 23:56:00+00:00  90452.0  90481.0  90420.0  90420.0   
7317756 2025-11-30 23:57:00+00:00  90412.0  90458.0  90396.0  90435.0   
7317757 2025-11-30 23:58:00+00:00  90428.0  90428.0  90362.0  90362.0   
7317758 2025-11-30 23:59:00+00:00  90363.0  90386.0  90362.0  90382.0   

           Volume  
7317754  0.531700  
7317755  0.055547  
7317756  0.301931  
7317757  4.591653  
7317758  0.410369

In [19]:
df_days = (
    df.groupby(df["Timestamp"].dt.date)
    .agg({"Low": "min", "High": "max", "Open": "first", "Close": "last"})
    .reset_index()
)
df_days.tail()

Timestamp      Low     High     Open    Close
5078  2025-11-26  86304.0  90646.0  87331.0  90477.0
5079  2025-11-27  90091.0  91926.0  90476.0  91325.0
5080  2025-11-28  90233.0  93091.0  91326.0  90913.0
5081  2025-11-29  90216.0  91179.0  90913.0  90832.0
5082  2025-11-30  90362.0  91969.0  90832.0  90382.0

In [21]:
df_days["Avg"] = (df_days["Low"] + df_days["High"]) / 2
df_days.tail()

Timestamp      Low     High     Open    Close      Avg
5078  2025-11-26  86304.0  90646.0  87331.0  90477.0  88475.0
5079  2025-11-27  90091.0  91926.0  90476.0  91325.0  91008.5
5080  2025-11-28  90233.0  93091.0  91326.0  90913.0  91662.0
5081  2025-11-29  90216.0  91179.0  90913.0  90832.0  90697.5
5082  2025-11-30  90362.0  91969.0  90832.0  90382.0  91165.5

In [25]:
intervals = []
start_idx = 0
price_base = df_days.loc[start_idx, "Avg"]

for i in range(1, len(df_days)):
    price_now = df_days.loc[i, "Avg"]
    change = abs(price_now - price_base) / price_base

    if change >= 0.10:
        interval = df_days.loc[start_idx:i]
        
        intervals.append({
            "start_date": df_days.loc[start_idx, "Timestamp"],
            "end_date": df_days.loc[i, "Timestamp"],
            "min_open": interval["Open"].min(),
            "max_close": interval["Close"].max(),
            "start_avg": price_base,
            "end_avg": price_now,
            "change": change,
        })

        start_idx = i + 1
        if start_idx >= len(df_days):
            break
        price_base = df_days.loc[start_idx, "Avg"]

df_intervals = pd.DataFrame(intervals)
df_intervals.tail()

start_date    end_date  min_open  max_close  start_avg   end_avg  \
335  2025-02-27  2025-04-23   76252.0    94273.0    84801.5   93335.0   
336  2025-04-24  2025-05-09   93730.0   103261.0    92867.5  103341.0   
337  2025-05-10  2025-07-11  100990.0   117579.0   103915.0  117032.5   
338  2025-07-12  2025-11-04  106470.0   124728.0   117599.0  103079.0   
339  2025-11-05  2025-11-18   92112.0   105972.0   101737.5   91471.0   

       change  
335  0.100629  
336  0.112779  
337  0.126233  
338  0.123470  
339  0.100912